In [0]:
#imports
from pyspark.sql import SQLContext
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder
from pyspark.ml import Pipeline
from pyspark.sql import Row
from pyspark.ml.recommendation import ALS
from pyspark.sql.functions import udf, col, when
import numpy as np

In [0]:
#reading the datasets : books details and users ratings
books_df = spark.read.csv('/Volumes/workspace/recommendation_system_data/books/books.csv',header=True, inferSchema=True) 
books_df.printSchema()

ratings_df = spark.read.csv('/Volumes/workspace/recommendation_system_data/books/ratings.csv',header=True, inferSchema=True)
ratings_df.printSchema()

root
 |-- id: integer (nullable = true)
 |-- book_id: integer (nullable = true)
 |-- best_book_id: integer (nullable = true)
 |-- work_id: integer (nullable = true)
 |-- books_count: integer (nullable = true)
 |-- isbn: string (nullable = true)
 |-- isbn13: double (nullable = true)
 |-- authors: string (nullable = true)
 |-- original_publication_year: double (nullable = true)
 |-- original_title: string (nullable = true)
 |-- title: string (nullable = true)
 |-- language_code: string (nullable = true)
 |-- average_rating: string (nullable = true)
 |-- ratings_count: string (nullable = true)
 |-- work_ratings_count: string (nullable = true)
 |-- work_text_reviews_count: string (nullable = true)
 |-- ratings_1: double (nullable = true)
 |-- ratings_2: integer (nullable = true)
 |-- ratings_3: integer (nullable = true)
 |-- ratings_4: integer (nullable = true)
 |-- ratings_5: integer (nullable = true)
 |-- image_url: string (nullable = true)
 |-- small_image_url: string (nullable = true)


In [0]:
#viewing each dataframe
ratings_df.display(5)
books_df.display(2)

book_id user_id rating 1 314 5 1 439 3 1 588 5 1 1169 4 1 1185 4 1 2077 4 1 2487 4 1 2900 5 1 3662 4 1 3922 5 1 5379 5 1 5461 3 1 5885 5 1 6630 5 1 7563 3 1 9246 1 1 10140 4 1 10146 5 1 10246 4 1 10335 4 1 10610 5 1 10944 5 1 11854 4 1 11927 4 1 12471 5 1 13282 5 1 13544 5 1 15494 5 1 16377 4 1 16913 5 1 17434 5 1 17663 5 1 17984 5 1 18031 5 1 18313 5 1 18361 4 1 20076 3 1 20467 3 1 20848 5 1 21228 5 1 21487 4 1 21713 5 1 22602 4 1 23576 4 1 23612 4 1 24326 5 1 24389 4 1 24499 5 1 24834 4 1 24845 5 1 25164 4 1 25182 5 1 25214 4 1 26145 4 1 26629 4 1 26661 4 1 28158 4 1 28767 5 1 29123 3 1 29703 5 1 30681 5 1 31001 4 1 32055 4 1 32305 5 1 32592 4 1 32635 5 1 32748 5 1 32923 5 1 33065 4 1 33697 4 1 33716 5 1 33872 5 1 33890 3 1 37284 5 1 37834 5 1 38080 4 1 38082 5 1 38475 4 1 39423 3 1 41074 3 1 42404 5 1 43985 4 1 44243 2 1 44397 5 1 45269 4 1 45493 5 1 46977 4 1 47476 4 1 47746 5 1 47800 5 1 48482 3 1 49298 4 1 50104 5 1 50342 3 1 51166 4 1 51460 3 1 51480 1 1 51838 5 1 52036 2 1 53245 4 2 1169 3 2 3022 4 2 3922 5 2 5115 4 2 5436 5 2 5461 4 2 5885 4 2 6063 1 2 6342 3 2 6630 5 2 8167 2 2 9731 4 2 10111 5 2 10140 3 2 10288 5 2 10509 2 2 10610 5 2 10751 3 2 10944 5 2 11285 4 2 11408 5 2 11691 4 2 11692 3 2 11868 5 2 11927 5 2 11945 5 2 12874 4 2 12946 5 2 13282 5 2 13794 1 2 14372 3 2 14546 5 2 14603 4 2 15604 4 2 16913 2 2 17434 5 2 17566 4 2 17643 1 2 17663 5 2 17984 5 2 18313 5 2 18361 4 2 19526 4 2 19724 5 2 19729 4 2 19942 5 2 21217 4 2 21228 4 2 21487 5 2 21676 5 2 21733 5 2 22602 4 2 23576 5 2 23612 5 2 24499 5 2 24834 4 2 25164 4 2 25182 5 2 26145 4 2 26629 4 2 27499 5 2 28767 4 2 30313 5 2 30681 4 2 30944 5 2 32055 4 2 32305 5 2 32592 4 2 32635 4 2 32748 5 2 32918 5 2 33065 5 2 33697 4 2 33716 5 2 33872 5 2 36099 5 2 37834 4 2 38082 5 2 42404 5 2 42508 4 2 42810 4 2 45269 4 2 45493 5 2 46421 5 2 46977 3 2 47476 3 2 47478 2 2 47800 5 2 48482 5 2 48559 5 2 48687 1 2 49298 5 2 50096 5 2 50104 5 2 50133 5 2 51166 5 2 51460 4 2 51838 4 2 52036 3 2 53292 5 3 314 3 3 588 1 3 2077 2 3 2487 3 3 2900 3 3 3662 4 3 4536 1 3 5115 4 3 5272 5 3 5461 2 3 5885 4 3 6063 5 3 6630 5 3 6634 3 3 7001 4 3 9246 1 3 9731 2 3 9771 3 3 10140 3 3 10246 1 3 10249 5 3 10509 1 3 10610 1 3 10751 1 3 10944 1 3 11285 2 3 11408 3 3 11599 4 3 11854 1 3 11927 4 3 12471 2 3 12946 4 3 13274 5 3 13282 5 3 13794 1 3 14546 5 3 15604 1 3 16377 1 3 16569 1 3 16913 4 3 17434 4 3 17663 4 3 18031 3 3 18313 5 3 19724 4 3 19942 4 3 19984 2 3 20076 3 3 20782 4 3 20848 4 3 21228 3 3 21487 3 3 21733 1 3 22602 3 3 23576 1 3 23612 3 3 24326 3 3 24389 3 3 25182 3 3 25214 1 3 26398 2 3 26629 4 3 28767 3 3 29703 1 3 30681 4 3 32305 1 3 32592 5 3 32635 4 3 32918 5 3 33065 1 3 33716 3 3 36099 4 3 36240 2 3 37284 1 3 37834 4 3 37855 3 3 38080 5 3 38082 3 3 38475 3 3 42404 5 3 43602 4 3 43985 2 3 46977 2 3 47746 5 3 48482 3 3 48687 1 3 49288 5 3 49289 5 3 49295 5 3 49297 5 3 49298 1 3 50096 5 3 50101 5 3 50102 5 3 50104 5 3 50133 5 3 51166 3 3 51460 2 3 52036 1 3 53292 5 4 439 5 4 1169 5 4 2324 5 4 2487 5 4 3739 5 4 3922 4 4 4606 1 4 5115 5 4 5436 5 4 6342 5 4 6630 4 4 8167 5 4 8178 5 4 9246 4 4 10140 4 4 11285 3 4 11691 5 4 11692 5 4 11868 3 4 11945 5 4 12381 5 4 12874 5 4 12946 5 4 13034 4 4 13776 4 4 13794 4 4 14192 4 4 14207 3 4 14546 5 4 14603 5 4 15604 3 4 17228 5 4 17643 5 4 17663 5 4 17984 5 4 18031 5 4 18313 5 4 19526 5 4 19724 5 4 19729 4 4 20406 2 4 20467 4 4 21217 4 4 21228 3 4 21487 5 4 21676 3 4 21733 5 4 23576 5 4 24326 5 4 25164 5 4 25182 5 4 25840 3 4 26579 3 4 26629 4 4 26661 5 4 27499 5 4 27834 5 4 27934 4 4 28767 5 4 29123 3 4 29703 5 4 30283 4 4 30313 5 4 30681 5 4 30944 5 4 32305 5 4 32338 4 4 32592 5 4 32745 4 4 32748 5 4 32918 5 4 32923 5 4 33065 5 4 33697 5 4 33716 4 4 33872 5 4 34688 4 4 36099 5 4 37284 3 4 37834 4 4 39423 5 4 42404 5 4 43985 5 4 44243 3 4 44397 5 4 45269 5 4 46482 5 4 47411 4 4 47730 5 4 47800 5 4 48482 3 4 48559 5 4 48687 5 4 49298 5 4 50102 5 4 51460 5 4 51838 4 4 52036 3 4 53245 5 4 53292 5 5 314 4 5 1169 5 5 1952 5 5 2324 5 5 2487 3

id book_id best_book_id work_id books_count isbn isbn13 authors original_publication_year original_title title language_code average_rating ratings_count work_ratings_count work_text_reviews_count ratings_1 ratings_2 ratings_3 ratings_4 ratings_5 image_url small_image_url 1 2767052 2767052 2792775 272 439023483 9.78043902348E12 Suzanne Collins 2008.0 The Hunger Games The Hunger Games (The Hunger Games, #1) eng 4.34 4780653 4942365 155254 66715.0 127936 560092 1481305 2706317 https://images.gr-assets.com/books/1447303603m/2767052.jpg https://images.gr-assets.com/books/1447303603s/2767052.jpg 2 3 3 4640799 491 439554934 9.78043955493E12 J.K. Rowling, Mary GrandPré 1997.0 Harry Potter and the Philosopher's Stone Harry Potter and the Sorcerer's Stone (Harry Potter, #1) eng 4.44 4602479 4800065 75867 75504.0 101676 455024 1156318 3011543 https://images.gr-assets.com/books/1474154022m/3.jpg https://images.gr-assets.com/books/1474154022s/3.jpg 3 41865 41865 3212258 226 316015849 9.78031601584E12 Stephenie Meyer 2005.0 Twilight Twilight (Twilight, #1) en-US 3.57 3866839 3916824 95009 456191.0 436802 793319 875073 1355439 https://images.gr-assets.com/books/1361039443m/41865.jpg https://images.gr-assets.com/books/1361039443s/41865.jpg 4 2657 2657 3275794 487 61120081 9.78006112008E12 Harper Lee 1960.0 To Kill a Mockingbird To Kill a Mockingbird eng 4.25 3198671 3340896 72586 60427.0 117415 446835 1001952 1714267 https://images.gr-assets.com/books/1361975680m/2657.jpg https://images.gr-assets.com/books/1361975680s/2657.jpg 5 4671 4671 245494 1356 743273567 9.78074327356E12 F. Scott Fitzgerald 1925.0 The Great Gatsby The Great Gatsby eng 3.89 2683664 2773745 51992 86236.0 197621 606158 936012 947718 https://images.gr-assets.com/books/1490528560m/4671.jpg https://images.gr-assets.com/books/1490528560s/4671.jpg 6 11870085 11870085 16827462 226 525478817 9.78052547881E12 John Green 2012.0 The Fault in Our Stars The Fault in Our Stars eng 4.26 2346404 2478609 140739 47994.0 92723 327550 698471 1311871 https://images.gr-assets.com/books/1360206420m/11870085.jpg https://images.gr-assets.com/books/1360206420s/11870085.jpg 7 5907 5907 1540236 969 618260307 9.7806182603E12 J.R.R. Tolkien 1937.0 The Hobbit or There and Back Again The Hobbit en-US 4.25 2071616 2196809 37653 46023.0 76784 288649 665635 1119718 https://images.gr-assets.com/books/1372847500m/5907.jpg https://images.gr-assets.com/books/1372847500s/5907.jpg 8 5107 5107 3036731 360 316769177 9.78031676917E12 J.D. Salinger 1951.0 The Catcher in the Rye The Catcher in the Rye eng 3.79 2044241 2120637 44920 109383.0 185520 455042 661516 709176 https://images.gr-assets.com/books/1398034300m/5107.jpg https://images.gr-assets.com/books/1398034300s/5107.jpg 9 960 960 3338963 311 1416524797 9.78141652479E12 Dan Brown 2000.0 Angels & Demons Angels & Demons (Robert Langdon, #1) en-CA 3.85 2001311 2078754 25112 77841.0 145740 458429 716569 680175 https://images.gr-assets.com/books/1303390735m/960.jpg https://images.gr-assets.com/books/1303390735s/960.jpg 10 1885 1885 3060926 3455 679783261 9.78067978327E12 Jane Austen 1813.0 Pride and Prejudice Pride and Prejudice eng 4.24 2035490 2191465 49152 54700.0 86485 284852 609755 1155673 https://images.gr-assets.com/books/1320399351m/1885.jpg https://images.gr-assets.com/books/1320399351s/1885.jpg 11 77203 77203 3295919 283 1594480001 9.78159448E12 Khaled Hosseini 2003.0 The Kite Runner The Kite Runner eng 4.26 1813044 1878095 59730 34288.0 59980 226062 628174 929591 https://images.gr-assets.com/books/1484565687m/77203.jpg https://images.gr-assets.com/books/1484565687s/77203.jpg 12 13335037 13335037 13155899 210 62024035 9.78006202404E12 Veronica Roth 2011.0 Divergent Divergent (Divergent, #1) eng 4.24 1903563 2216814 101023 36315.0 82870 310297 673028 1114304 https://images.gr-assets.com/books/1328559506m/13335037.jpg https://images.gr-assets.com/books/1328559506s/13335037.jpg 13 5470 5470 153313 995 451524934 9.78045152494E12 George Orwell, Erich Fromm, C

In [0]:
#spliting the test and train data
training_df, validation_df = ratings_df.randomSplit([.8, .2])

In [0]:
#hyperparameters
iterations = 10
regularization_parameter = 0.1
rank= 4

In [0]:
#creating a ALS model, training and testing using the model
#also find the RMSE 
als = ALS(maxIter=iterations, regParam=regularization_parameter, rank=4, userCol="user_id", itemCol="book_id", ratingCol="rating")
model = als.fit(training_df)
predictions = model.transform(validation_df)
new_predictions = predictions.filter(col('prediction') != np.nan)
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating", predictionCol="prediction")
rmse = evaluator.evaluate(new_predictions)
print("Root-mean-square error = " + str(rmse))

Root-mean-square error = 0.8939823911691192


In [0]:
import os
os.environ["SPARKML_TEMP_DFS_PATH"] = "/Volumes/workspace/recommendation_system_data/cv_caching/"


In [0]:
#finding the best model through cross validation and hperparameter tuning
#using the paramglid and cross validation
als = ALS(maxIter=iterations, regParam=regularization_parameter, rank=rank, userCol="user_id", itemCol="book_id", ratingCol="rating")
paramGrid = ParamGridBuilder() \
    .addGrid(als.regParam, [0.1, 0.01, 0.18]) \
    .addGrid(als.rank, range(4, 6)) \
    .build()
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating", predictionCol="prediction")
crossval = CrossValidator(estimator=als,
                          estimatorParamMaps=paramGrid,
                          evaluator=evaluator,
                          numFolds=5)
cv_model = crossval.fit(training_df)
final_model = cv_model.bestModel

In [0]:
#prediction using the selected model
predictions = final_model.transform(validation_df)
predictions = predictions.filter(col('prediction') != np.nan)
rmse = evaluator.evaluate(predictions)
print("the rmse for optimal grid parameters with cross validation is: {}".format(rmse))
predictions.show(n = 10)

the rmse for optimal grid parameters with cross validation is: 0.8939823911691192
+-------+-------+------+----------+
|book_id|user_id|rating|prediction|
+-------+-------+------+----------+
|    348|  18714|     4|  3.565439|
|    452|  28057|     4| 3.9035773|
|    472|  41014|     5|  4.339942|
|    671|  28057|     4| 3.9046853|
|    698|  28057|     4| 3.9500213|
|    827|  18714|     3| 3.9161487|
|    858|  18714|     5| 4.3690095|
|    972|  28057|     5| 3.6693347|
|   1012|  28057|     3| 3.8173797|
|   1170|  34159|     5|  4.270044|
+-------+-------+------+----------+
only showing top 10 rows


In [0]:

# Generate top 10 books recommendations for each user
userRecommends = final_model.recommendForAllUsers(10)
# Generate top 10 user recommendations for each movie
bookRecommends = final_model.recommendForAllItems(10)


In [0]:
#writing the books recommendations for each users and vise versa
userRecommends.write.saveAsTable("workspace.recommendation_system_data.books_recommendations")
bookRecommends.write.saveAsTable("workspace.recommendation_system_data.users_recommendations")

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-8305339459285150>, line 2
      1 #writing the books recommendations for each users and vise versa
----> 2 flat_userRec.write.saveAsTable("workspace.recommendation_system_data.books_recommendations")
      3 flat_bookRec.write.saveAsTable("workspace.recommendation_system_data.users_recommendations")

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/readwriter.py:737, in DataFrameWriter.saveAsTable(self, name, format, mode, partitionBy, **options)
    735 self._write.table_name = name
    736 self._write.table_save_method = "save_as_table"
--> 737 _, _, ei = self._spark.client.execute_command(
    738     self._write.command(self._spark.client), self._write.observations
    739 )
    740 self._callback(ei)

File /databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/client/core.py:1556, 